In [ ]:
import csv

input_file = r"C:\Users\varun\OneDrive\Desktop\major\anomaly\newfolder\data\contract.txt"
output_file = r"C:\Users\varun\OneDrive\Desktop\major\anomaly\newfolder\confinall.txt"

with open(input_file, 'r') as infile, open(output_file, 'w', newline='') as outfile:
    reader = csv.reader(infile, delimiter='\t') 
    writer = csv.writer(outfile, delimiter='\t') 
    header = next(reader)
    writer.writerow(header)

    for row in reader:
        if len(row) >= 2 and row[1] == '2':
            writer.writerow(row)

print(f"✅ Nodes with contract value 2 written to {output_file}")


✅ Nodes with contract value 2 written to C:\Users\varun\OneDrive\Desktop\major\anomaly\newfolder\confinall.txt


In [ ]:
import pandas as pd
import os


folder_path = r"D:\bhavya\daywise1" 
flipping_nodes_file = r'C:\Users\varun\OneDrive\Desktop\major\anomaly\newfolder\confinall.txt' 
output_file = 'filtered_flipping_nodes_transactions.txt'


flipping_df = pd.read_csv(flipping_nodes_file, sep='\t', header=0, names=['Node', 'Contract_Type'])
flipping_nodes = set(flipping_df['Node'].astype(str).str.strip())
print("Loaded flipping nodes:", list(flipping_nodes)[:10])


filtered_transactions = []

for filename in os.listdir(folder_path):
    if filename.endswith('.txt') or filename.endswith('.csv'):
        print(f"Reading file: {filename}")
        file_path = os.path.join(folder_path, filename)
        
        try:
           
            df = pd.read_csv(file_path, sep='\t', header=None,
                             names=['timestamp', 'date', 'time', 'from', 'to', 'fromiscontract', 'toiscontract', 'value'])

            
            df['from'] = df['from'].astype(str).str.strip()
            df['to'] = df['to'].astype(str).str.strip()

        
            filtered_df = df[df['from'].isin(flipping_nodes) | df['to'].isin(flipping_nodes)]

            if not filtered_df.empty:
                filtered_transactions.append(filtered_df)
            else:
                print(f"No matches in {filename}")

        except Exception as e:
            print(f"Error processing {filename}: {e}")


if filtered_transactions:
    final_df = pd.concat(filtered_transactions, ignore_index=True)
    final_df.to_csv(output_file, sep='\t', index=False)
    print(f"Filtered transactions saved to {output_file}")
else:
    print("No matching transactions found in any file.")


Loaded flipping nodes: ['67566289', '58931860', '71866620', '67751773', '52023087', '71362551', '65551494', '62555075', '67783115', '72279645']
Reading file: 2016-02-13.txt
Reading file: 2016-02-14.txt
Reading file: 2016-02-15.txt
Reading file: 2016-02-16.txt
Reading file: 2016-02-17.txt
Reading file: 2016-02-18.txt
Reading file: 2016-02-19.txt
Reading file: 2016-02-20.txt
Reading file: 2016-02-21.txt
Reading file: 2016-02-22.txt
Reading file: 2016-02-23.txt
Reading file: 2016-02-24.txt
Reading file: 2016-02-25.txt
Reading file: 2016-02-26.txt
Reading file: 2016-02-27.txt
Reading file: 2016-02-28.txt
Reading file: 2016-02-29.txt
Reading file: 2016-03-01.txt
Reading file: 2016-03-02.txt
Reading file: 2016-03-03.txt
Reading file: 2016-03-04.txt
Reading file: 2016-03-05.txt
Reading file: 2016-03-06.txt
Reading file: 2016-03-07.txt
Reading file: 2016-03-08.txt
Reading file: 2016-03-09.txt
Reading file: 2016-03-10.txt
Reading file: 2016-03-11.txt
Reading file: 2016-03-12.txt
Reading file: 2

c:\Users\varun\anaconda3\envs\MINI2\lib\site-packages\IPython\core\interactiveshell.py:3552: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


Reading file: 2020-02-05.txt
Reading file: 2020-02-06.txt
Reading file: 2020-02-07.txt
Reading file: 2020-02-08.txt
Reading file: 2020-02-09.txt
Reading file: 2020-02-10.txt
Reading file: 2020-02-11.txt
Reading file: 2020-02-12.txt
Reading file: 2020-02-13.txt
Reading file: 2020-02-14.txt
Reading file: 2020-02-15.txt
Reading file: 2020-02-16.txt
Reading file: 2020-02-17.txt
Reading file: 2020-02-18.txt
Reading file: 2020-02-19.txt
Reading file: 2020-02-20.txt
Reading file: 2020-02-21.txt
Reading file: 2020-02-22.txt
Reading file: 2020-02-23.txt
Reading file: 2020-02-24.txt
Reading file: 2020-02-25.txt
Reading file: 2020-02-26.txt
Reading file: 2020-02-27.txt
Reading file: 2020-02-28.txt
Reading file: 2020-02-29.txt
Reading file: 2020-03-01.txt
Reading file: 2020-03-02.txt
Reading file: 2020-03-03.txt
Reading file: 2020-03-04.txt
Reading file: 2020-03-05.txt
Reading file: 2020-03-06.txt
Reading file: 2020-03-07.txt
Reading file: 2020-03-08.txt
Reading file: 2020-03-09.txt
Reading file: 

In [ ]:
import pandas as pd
import re


file_path = 'filtered_flipping_nodes_transactions.txt' 
output_summary_file = 'node_flipping_summary.txt'
output_high_value_flips = 'high_value_flips.txt'
HIGH_VALUE_THRESHOLD = 1e18


df = pd.read_csv(file_path, sep=r'\s+', header=0)


df = df.applymap(lambda x: x.strip() if isinstance(x, str) else x)


df['fromiscontract'] = pd.to_numeric(df['fromiscontract'], errors='coerce')
df['toiscontract'] = pd.to_numeric(df['toiscontract'], errors='coerce')
df['value'] = pd.to_numeric(df['value'], errors='coerce')


df['datetime'] = pd.to_datetime(df['date'] + ' ' + df['time'], errors='coerce')

df = df.dropna(subset=['datetime'])


from_df = df[['from', 'fromiscontract', 'datetime', 'value']].rename(columns={'from': 'node', 'fromiscontract': 'iscontract'})
to_df = df[['to', 'toiscontract', 'datetime', 'value']].rename(columns={'to': 'node', 'toiscontract': 'iscontract'})


node_df = pd.concat([from_df, to_df], ignore_index=True)


node_df['node'] = node_df['node'].astype(str).str.strip()
node_df['iscontract'] = pd.to_numeric(node_df['iscontract'], errors='coerce')
node_df['value'] = pd.to_numeric(node_df['value'], errors='coerce')

node_df = node_df.dropna(subset=['iscontract'])


node_df['iscontract'] = node_df['iscontract'].astype(int)


node_df = node_df.sort_values(by=['node', 'datetime'])


def count_flips(group):
    changes = group['iscontract'] != group['iscontract'].shift()
    flips = changes.sum() - 1  # First appearance isn't a flip
    flip_times = group.loc[changes, 'datetime'].tolist()
    return pd.Series({'flips': max(flips, 0), 'flip_times': flip_times})

flip_summary = node_df.groupby('node').apply(count_flips).reset_index()
flip_summary.to_csv(output_summary_file, sep='\t', index=False)
print(f"Flip summary saved to: {output_summary_file}")


node_df['prev_iscontract'] = node_df.groupby('node')['iscontract'].shift()
node_df['flipped'] = node_df['iscontract'] != node_df['prev_iscontract']

high_value_flips = node_df[(node_df['flipped']) & (node_df['value'] >= HIGH_VALUE_THRESHOLD)]
high_value_flips[['node', 'datetime', 'iscontract', 'value']].to_csv(output_high_value_flips, sep='\t', index=False)
print(f"High-value flips saved to: {output_high_value_flips}")


✅ Flip summary saved to: node_flipping_summary.txt
✅ High-value flips saved to: high_value_flips.txt


In [ ]:
import plotly.express as px


hvf_df = pd.read_csv(r"C:\Users\varun\OneDrive\Desktop\major\high_value_flips.txt", sep='\t')


hvf_df['datetime'] = pd.to_datetime(hvf_df['datetime'])


hvf_df = hvf_df.sort_values(by='datetime')


fig = px.scatter(
    hvf_df,
    x='datetime',
    y='node',
    size='value',
    color='iscontract',
    hover_data=['node', 'value'],
    title='High-Value Flips Over Time',
    labels={'node': 'Node ID', 'datetime': 'Flip Timestamp', 'value': 'Flip Value'},
    template='plotly_white'
)


fig.update_layout(
    xaxis_title='Timestamp',
    yaxis_title='Node ID',
    hovermode='closest',
    xaxis_rangeslider_visible=True,
    showlegend=True
)

fig.show()


In [ ]:
import pandas as pd
import plotly.graph_objects as go
from datetime import timedelta
import re

flip_summary = pd.read_csv('node_flipping_summary.txt', sep='\t')

def clean_flip_times(text):
    matches = re.findall(r"Timestamp\('([^']+)'\)", text)
    return pd.to_datetime(matches)

flip_summary['flip_times'] = flip_summary['flip_times'].apply(clean_flip_times)

all_flips = pd.to_datetime([ts for sublist in flip_summary['flip_times'] for ts in sublist])

flip_series = pd.Series(1, index=all_flips)
flip_series = flip_series.resample('1D').sum()

fig = go.Figure()

fig.add_trace(go.Scatter(x=flip_series.index, y=flip_series.values, mode='lines+markers', name='Flip Frequencies'))

fig.update_layout(
    title="Flip Frequencies Over Time (All Nodes)",
    xaxis_title="Date",
    yaxis_title="Number of Flips",
    template="plotly_white",
    hovermode="x unified", 
    xaxis_rangeslider_visible=True  
)

fig.show()

burst_gap = timedelta(hours=1)

burst_records = []

for idx, row in flip_summary.iterrows():
    node = row['node']
    times = row['flip_times']
    
    if len(times) > 1:
        times = sorted(times)
        burst_start = times[0]
        burst = [burst_start]
        
        for i in range(1, len(times)):
            if times[i] - times[i-1] <= burst_gap:
                burst.append(times[i])
            else:
                if len(burst) > 1:
                    burst_records.append({'node': node, 'start': burst[0], 'end': burst[-1], 'count': len(burst)})
                burst = [times[i]]
        
        if len(burst) > 1:
            burst_records.append({'node': node, 'start': burst[0], 'end': burst[-1], 'count': len(burst)})

burst_df = pd.DataFrame(burst_records)

if not burst_df.empty:
    fig_burst = go.Figure()

    for node in burst_df['node'].unique():
        node_bursts = burst_df[burst_df['node'] == node]

        fig_burst.add_trace(go.Scatter(
            x=node_bursts['start'],
            y=[node]*len(node_bursts),
            mode='markers',
            name=f'Node {node}',
            marker=dict(size=node_bursts['count']*10), 
            text=[f"Node {node}<br>Start: {start}<br>End: {end}<br>Count: {count}" for start, end, count in zip(node_bursts['start'], node_bursts['end'], node_bursts['count'])], 
            hoverinfo="text"
        ))

    fig_burst.update_layout(
        title="Burst Flip Events per Node",
        xaxis_title="Time",
        yaxis_title="Node ID",
        template="plotly_white",
        hovermode="closest", 
        xaxis_rangeslider_visible=True 
    )

    
    fig_burst.show()
else:
    print("No burst events detected (flips within 1 hour for any node).")


In [ ]:
import pandas as pd
import plotly.graph_objects as go
from datetime import timedelta
import re

flip_summary = pd.read_csv('node_flipping_summary.txt', sep='\t')

def clean_flip_times(text):
    matches = re.findall(r"Timestamp\('([^']+)'\)", text)
    return pd.to_datetime(matches)

flip_summary['flip_times'] = flip_summary['flip_times'].apply(clean_flip_times)

all_flips = pd.to_datetime([ts for sublist in flip_summary['flip_times'] for ts in sublist])

flip_series = pd.Series(1, index=all_flips)
flip_series = flip_series.resample('1D').sum()

fig = go.Figure()

fig.add_trace(go.Scatter(x=flip_series.index, y=flip_series.values, mode='lines+markers', name='Flip Frequencies'))

fig.update_layout(
    title="Flip Frequencies Over Time (All Nodes)",
    xaxis_title="Date",
    yaxis_title="Number of Flips",
    template="plotly_white",
    hovermode="x unified", 
    xaxis_rangeslider_visible=True 
)

fig.show()

burst_gap = timedelta(minutes=30)

burst_records = []

for idx, row in flip_summary.iterrows():
    node = row['node']
    times = row['flip_times']
    
    if len(times) > 1:
        times = sorted(times)
        burst_start = times[0]
        burst = [burst_start]
        
        for i in range(1, len(times)):
            if times[i] - times[i-1] <= burst_gap:
                burst.append(times[i])
            else:
                if len(burst) > 1:
                    burst_records.append({'node': node, 'start': burst[0], 'end': burst[-1], 'count': len(burst)})
                burst = [times[i]]
        

        if len(burst) > 1:
            burst_records.append({'node': node, 'start': burst[0], 'end': burst[-1], 'count': len(burst)})


burst_df = pd.DataFrame(burst_records)


if not burst_df.empty:
    fig_burst = go.Figure()

    for node in burst_df['node'].unique():
        node_bursts = burst_df[burst_df['node'] == node]
        
     
        fig_burst.add_trace(go.Scatter(
            x=node_bursts['start'],
            y=[node]*len(node_bursts),
            mode='markers',
            name=f'Node {node}',
            marker=dict(size=node_bursts['count']*10),  # Adjust marker size based on count
            text=[f"Node {node}<br>Start: {start}<br>End: {end}<br>Count: {count}" for start, end, count in zip(node_bursts['start'], node_bursts['end'], node_bursts['count'])],  # Show details on hover
            hoverinfo="text"
        ))


    fig_burst.update_layout(
        title="Burst Flip Events per Node",
        xaxis_title="Time",
        yaxis_title="Node ID",
        template="plotly_white",
        hovermode="closest", 
        xaxis_rangeslider_visible=True 
    )


    fig_burst.show()
else:
    print("No burst events detected (flips within 1 hour for any node).")
